# Exercise 8: Part-of-Speech tagging using Markov Models

We will be doing Part-of-Speech (POS) tagging. This is a common problem in natural language processing that tries to assign grammatical tags to each word in a sentence. 
Often this task is posed as a sequence labeling task that can be modeled as a Markov chain.

Let's consider an example:
We have a sentence $Y_{0:T} = $ `Time flies like an arrow.`  and want to predict the corresponding POS tags that we model as a latent sequence $X_{0:T} =$ `NOUN VERB CONJ DET NOUN`. 
This example already reveals the challenge of this task which requires us to take context information into account, since the word `flies` could also be classified as `NOUN` in another context.


In the following exercise, we will apply the algorithm that we introduced in lecture 15 (slide 36) to this problem. 

### 0. Download and prepare the data

In [1]:
%pip install nltk

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [2]:
# Importing libraries
import nltk
import numpy as np
import pandas as pd
import random
from sklearn.model_selection import train_test_split
from functools import partial

 
# download the treebank corpus from nltk
nltk.download('treebank')
 
# download the universal tagset from nltk
nltk.download('universal_tagset')
 
# reading the Treebank tagged sentences
nltk_data = list(nltk.corpus.treebank.tagged_sents(tagset='universal'))

# split data into training and validation set in the ratio 80:20
train_set,test_set =train_test_split(nltk_data,train_size=0.80,test_size=0.20,random_state = 101)

[nltk_data] Downloading package treebank to
[nltk_data]     C:\Users\Soenke\AppData\Roaming\nltk_data...
[nltk_data]   Package treebank is already up-to-date!
[nltk_data] Downloading package universal_tagset to
[nltk_data]     C:\Users\Soenke\AppData\Roaming\nltk_data...
[nltk_data]   Package universal_tagset is already up-to-date!


In [3]:
# create list of train and test tagged words (ignore sentence boundaries)
train_data = [ tup for sent in train_set for tup in sent ]
test_data = [ tup for sent in test_set for tup in sent ]
print(len(train_data))
print(len(test_data))

80310
20366


In [4]:
# check some of the tagged words.
train_data[:5]
print(train_data[5][1])

ADP


In [5]:
# use set datatype to check how many unique tags are present in training data
tags = {tag for word,tag in train_data}
tag_vocab = {tag: i for i, tag in enumerate(tags)}
 
# check total words in vocabulary
words = {word for word,tag in train_data}
word_vocab = {word: i for i, word in enumerate(words)}

In [6]:
print(tags)
print(tag_vocab)
print(words)
print(word_vocab)

{'DET', '.', 'ADP', 'ADJ', 'X', 'CONJ', 'PRON', 'PRT', 'ADV', 'NUM', 'NOUN', 'VERB'}
{'DET': 0, '.': 1, 'ADP': 2, 'ADJ': 3, 'X': 4, 'CONJ': 5, 'PRON': 6, 'PRT': 7, 'ADV': 8, 'NUM': 9, 'NOUN': 10, 'VERB': 11}
{'buses', 'lover', 'school-district', '1987-88', 'what', 'types', 'Individual', 'operation', 'Ill', 'Kurland', 'politely', 'Manchester', 'Wis.', 'so-called', 'interim', 'bidder', 'halted', 'dividend', '27', 'promote', '*-104', 'Contel', 'still', 'No', 'telegraph', 'extra', 'indicator', 'Walker', '*T*-183', 'rapidly', 'interrogation', 'Caters', '*-89', 'debts', 'easing', 'logic', 'lifes', 'letter-writing', 'obtained', 'belonging', 'outlays', 'manner', 'Gunmen', 'Bangkok', 'pocket', 'percentage', 'Shapiro', 'driver', 'Phillip', 'cloth', 'Drexel', 'overcome', 'interviewed', 'cues', 'parties', 'currency', '14-hour', 'noticed', '*T*-41', '90', 'offsetting', 'Ed', 'MacLellan', "'86", 'above', 'closely', 'Her', 'am', 'role', 'asserted', 'There', 'provide', 'increased', 'debate', 'strict',

## 1. Precomputing probabilities ("Training")  
#### [1] (a) Compute the transition probability
First we need to compute the transition probability, i.e. the probability that one POS tag follows on another: $p(x_t|x_{t-1})$

For this purpose, we can just pre-compute the entire table of conditional probabilities based on the counts from the training set. 

In [7]:
def compute_transition(train_data, tag_vocab):
    p_transition = np.zeros((len(tag_vocab),len(tag_vocab)))
    # TODO

    # Count number of occured transitions
    for i in range(1, len(train_data)):
        curr_tag = tag_vocab[train_data[i][1]]
        prev_tag = tag_vocab[train_data[i-1][1]]
        p_transition[prev_tag, curr_tag]+= 1

    # Normalize counts to obtain valid probabilities
    row_sums = p_transition.sum(axis=1, keepdims=True)
    p_transition /= row_sums

    return p_transition

In [8]:
p_transition = compute_transition(train_data, tag_vocab)
tags_df = pd.DataFrame(p_transition, columns = list(tags), index=list(tags))
display(tags_df)

DET         .       ADP       ADJ         X      CONJ      PRON  \
DET   0.006037  0.017393  0.009918  0.206411  0.045134  0.000431  0.003306   
.     0.172210  0.092382  0.092918  0.046137  0.025644  0.060086  0.068777   
ADP   0.320931  0.038724  0.016958  0.107062  0.034548  0.001012  0.069603   
ADJ   0.005243  0.066019  0.080583  0.063301  0.020971  0.016893  0.000194   
X     0.056890  0.160869  0.142226  0.017682  0.075726  0.010379  0.054200   
CONJ  0.123491  0.035126  0.055982  0.113611  0.009330  0.000549  0.060373   
PRON  0.009567  0.041913  0.022323  0.070615  0.088383  0.005011  0.006834   
PRT   0.101370  0.045010  0.019569  0.082975  0.012133  0.002348  0.017613   
ADV   0.071373  0.139255  0.119472  0.130721  0.022886  0.006982  0.012025   
NUM   0.003570  0.119243  0.037487  0.035345  0.202428  0.014281  0.001428   
NOUN  0.013106  0.240094  0.176827  0.012584  0.028825  0.042454  0.004659   
VERB  0.133610  0.034807  0.092357  0.066390  0.215930  0.005433  0.035543   

           PRT       ADV       NUM      NOUN      VERB  
DET   0.000287  0.012074  0.022855  0.635906  0.040247  
.     0.002790  0.052575  0.078219  0.218562  0.089700  
ADP   0.001266  0.014553  0.063275  0.323589  0.008479  
ADJ   0.011456  0.005243  0.021748  0.696893  0.011456  
X     0.185086  0.025754  0.003075  0.061695  0.206419  
CONJ  0.004391  0.057080  0.040615  0.349067  0.150384  
PRON  0.014123  0.036902  0.006834  0.212756  0.484738  
PRT   0.001174  0.009393  0.056751  0.250489  0.401174  
ADV   0.014740  0.081458  0.029868  0.032196  0.339022  
NUM   0.026062  0.003570  0.184220  0.351660  0.020707  
NOUN  0.043935  0.016895  0.009144  0.262344  0.149134  
VERB  0.030663  0.083886  0.022836  0.110589  0.167956

#### [1] (b) Compute the emission probability
Additionally, we need to compute the emission probability, i.e. the probability that a POS tag is associated with a specific word: $p(y_t|x_t)$.

For this purpose, we can just pre-compute the entire table of conditional probabilities based on the counts from the training set.

In [9]:
def compute_emission(train_data, tag_vocab, word_vocab):
    p_emission = np.zeros((len(word_vocab),len(tag_vocab)))
    # TODO

    for i in range(len(train_data)):
        # obtain row/word:
        row = word_vocab[train_data[i][0]]
        
        # obtain col/tag:
        col = tag_vocab[train_data[i][1]]

        # increment in matrix
        p_emission[row, col] += 1

    # Normalize counts to obtain valid probabilities
    row_sums = p_emission.sum(axis=1, keepdims=True)
    p_emission /= row_sums 
    return p_emission

In [10]:
p_emission = compute_emission(train_data, tag_vocab, word_vocab)
words_df = pd.DataFrame(p_emission, columns = list(tags), index=list(words))
display(words_df)

DET    .  ADP  ADJ    X  CONJ      PRON  PRT  ADV  NUM  \
buses            0.000000  0.0  0.0  0.0  0.0   0.0  0.000000  0.0  0.0  0.0   
lover            0.000000  0.0  0.0  0.0  0.0   0.0  0.000000  0.0  0.0  0.0   
school-district  0.000000  0.0  0.0  0.0  0.0   0.0  0.000000  0.0  0.0  0.0   
1987-88          0.000000  0.0  0.0  0.0  0.0   0.0  0.000000  0.0  0.0  1.0   
what             0.078947  0.0  0.0  0.0  0.0   0.0  0.921053  0.0  0.0  0.0   
...                   ...  ...  ...  ...  ...   ...       ...  ...  ...  ...   
37-year-old      0.000000  0.0  0.0  1.0  0.0   0.0  0.000000  0.0  0.0  0.0   
insider          0.000000  0.0  0.0  0.0  0.0   0.0  0.000000  0.0  0.0  0.0   
inspired         0.000000  0.0  0.0  0.0  0.0   0.0  0.000000  0.0  0.0  0.0   
incurred         0.000000  0.0  0.0  0.0  0.0   0.0  0.000000  0.0  0.0  0.0   
subminimum       0.000000  0.0  0.0  0.0  0.0   0.0  0.000000  0.0  0.0  0.0   

                 NOUN  VERB  
buses             1.0   0.0  
lover             1.0   0.0  
school-district   1.0   0.0  
1987-88           0.0   0.0  
what              0.0   0.0  
...               ...   ...  
37-year-old       0.0   0.0  
insider           1.0   0.0  
inspired          0.0   1.0  
incurred          0.0   1.0  
subminimum        1.0   0.0  

[11052 rows x 12 columns]

#### [1] (c) Compute the unigram probabilities
Finally, we need to compute the unigram probability of observing a given word: $p(y)$.
Analogously for a given POS-tag: $p(x)$

Again, we compute this probability on the counts from the training set.

In [11]:
def compute_unigrams(train_data, word_vocab, tag_vocab):
    p_y = np.zeros(len(word_vocab))
    p_x = np.zeros(len(tag_vocab))
    
    # count words and POS tags in the training data
    for word, tag in train_data:
        if word in word_vocab:
            p_y[word_vocab[word]] += 1
        if tag in tag_vocab:
            p_x[tag_vocab[tag]] += 1
    
    # normalize counts to get probabilities
    p_y = p_y / p_y.sum()
    p_x = p_x / p_x.sum()
    
    return p_y, p_x

In [12]:
p_y, p_x = compute_unigrams(train_data, word_vocab, tag_vocab)
words_df = pd.DataFrame(p_y, index=list(words))
display(words_df)
tag_df = pd.DataFrame(p_x, index=list(tags))
display(tag_df)

0
buses            0.000037
lover            0.000012
school-district  0.000012
1987-88          0.000012
what             0.000473
...                   ...
37-year-old      0.000012
insider          0.000012
inspired         0.000012
incurred         0.000025
subminimum       0.000025

[11052 rows x 1 columns]

0
DET   0.086627
.     0.116063
ADP   0.098394
ADJ   0.064127
X     0.064786
CONJ  0.022687
PRON  0.027332
PRT   0.031814
ADV   0.032101
NUM   0.034877
NOUN  0.285967
VERB  0.135226

#### Add an unknown token:
Now we computed these probabilities from the training data. Unfortunately evaluating on unseen data can lead to problems if we encounter words that we did not see before. There are many ways to deal with this. One option is to replace unseen words with an `<UNK>` token. We set the emission probability to be uniform, s.t. the algorithm has to rely on the transition probability to figure out the POS-tag.

In [13]:
eps= 1e-12
unk_id = len(word_vocab)
word_vocab["<UNK>"] = unk_id
p_y -= eps
p_y = np.concatenate([p_y,np.array([p_y.shape[0] * eps])], axis=0)
p_emission = np.concatenate([p_emission,np.ones_like(p_emission[:1])/len(p_emission[0])], axis=0)
def turn_unk(w):
    if w not in word_vocab:
        return "<UNK>"
    else:
        return w
test_data = [(turn_unk(w),t) for w,t in test_data]

## [1] 2. Numerical Stability
We have now computed all the probabilities that we need to apply the algorithm from the lecture.
However, if we just apply this algorithm naively, we will run into problems of numerical stability. 
To illustrate this, let's compute the probability of a random sequence of tags $p(x_0,x_1,...,x_N)$:

In [14]:
N = 100 
idx = np.random.choice(list(tag_vocab.values()), size=N+1)
p_seq = np.prod(p_x[idx]) # TODO
print(p_seq)

5.490409442972541e-121


As you can see, although we are multiplying non-zero probabilities, we end up with a probability of zero very quickly as we increase $N$. 

This problem can be avoided by performing computations in log-space. This means that we take the logarithm of all probability values before peforming any computations with them. 
This will turn all products into summations and divisions into subtractions. 
Let's try this trick on the task above and compute the value of $\log p(x_0,x_1,...,x_N)$

In [15]:
log_p_seq = np.sum(np.log(p_x[idx])) # TODO
print(log_p_seq)

-276.9097934197626


Now if we convert this back to $p(x_0,...,x_N)$, by taking the exponential, we will still end up with zero. So what does this help us? 

Here we can make use of the fact that the logarithm is a monotone increasing function, which means in particular that 
$$
\mathrm{argmax}_x p(x) = \mathrm{argmax}_x \log p(x)
$$ 
This is useful in cases like this one where the exact probability is not of interest, but we just want to know the position of the maximum value of a particular function. 

Finally, we need to deal with the situation where we want to take the logarithm of a sum of probabilities. 
In that case, we cannot just "pull the log through". 
Instead we need to use the log-sum-exp trick:
$$
\log \sum_{i=1}^{M} p(x_i) = b + \log \sum_{i=1}^M \exp ((\log p(x_i)) - b)   
$$
with $b = \max_i \log p(x_i)$. 
Please read this short explanation to understand why/how this works: [http://wittawat.com/posts/log-sum_exp_underflow.html](http://wittawat.com/posts/log-sum_exp_underflow.html)

In the following implementation, we will exclusively work with log-probabilities and use the log-sum-exp trick wherever we encounter a sum.
To prepare for this, we now convert all probabilities into log-probabilities and add a small `eps` term to all values to avoid $\log(0)$.

In [16]:
eps= 1e-12
log_p_y = np.log(p_y + eps)
log_p_x = np.log(p_x + eps)
log_p_transition = np.log(p_transition + eps)
log_p_emission = np.log(p_emission + eps)

## 3. The algorithm
Now that we have implemented the emission and transition probabilities, we can use them to compute the predictions $p(x_t|Y)$ for all $t=0,\ldots,n$ by applying the algorithm from the lecture.
Note that we $x$ is a discrete variable (we only have a limited vocabulary $\mathcal{X}$), which allows us to evaluate the integral expressions by carrying out a sum.

#### Please read all subtasks carefully before starting your implementation! 

#### [2] (a) Predict: 
Please compute the prediction step here. Note that you need to apply the log-sum-exp trick here and use numpy operations to efficiently compute the probabilities for all possible $x_t$ at the current timestep $t$. 

$$ p(x_t|Y_{0:t-1}) = \sum_{x_{t-1} \in \mathcal{X}} p(x_t|x_{t-1}) p(x_{t-1}|Y_{0:t-1}) $$

In [23]:
def predict(t, log_p_update, log_p_transition):
    """
    Args:
        t (int): Current timestep.
        log_p_update (np.array): `log p(x_t|y_{0:t})` array of shape [T+1, len(tag_vocab)].
        log_p_transition (np.array): `log p(x_t|x_{t-1})` array of shape [len(tag_vocab), len(tag_vocab)].
    
    Returns: 
        np.array: `log p(x_t|y_{0:t-1})` for timestep t. Array of shape [len(tag_vocab)]
    """
    log_p_predict_unnormalized = np.zeros(len(tag_vocab))

    # To obtain b
    ### For every possible x_t there is a unique b
    b = np.zeros(len(tag_vocab))
   
    # Initialize an array to store unnormalized log probabilities for the current state x_t
    for state_t in range(len(tag_vocab)):
        b[state_t] = np.finfo(float).min
        # Iterate over possible previous states x_{t-1}
        for state_t_minus_1 in range(len(tag_vocab)):
            # get the maximum log-summand
            b[state_t] = np.maximum(b[state_t], log_p_update[t, state_t_minus_1] + log_p_transition[state_t_minus_1, state_t])

    
    # Use log-sum-exp trick to avoid numerical instability

    # Initialize log_p_predict with values equal to b
    log_p_predict = b

    # Now add the log-sums to every output (current state x_t)
    for state_t in range(len(tag_vocab)):
        # To calculate the log-sum, initialize the sum
        total_sum = 0
        
        # Iterate over possible previous states x_{t-1} to get the sum
        for state_t_minus_1 in range(len(tag_vocab)):
            # Accumulate log probabilities for the current state x_t
            total_sum += np.exp(log_p_update[t, state_t_minus_1] + log_p_transition[state_t_minus_1, state_t] - b[state_t])
        
        # we need to add the log of the sum
        log_p_predict[state_t] += np.log(total_sum)
        
    #print(log_p_predict)
    
    return log_p_predict

#### [2] (b) Update: 
Please compute the update step here. Note that you need to perform the operations in log-space here and use numpy operations to efficiently compute the probabilities for all possible $x_t$ at the current timestep $t$. 

$$ p(x_t|Y_{1:t}) = p(y_t|x_t) \frac{p(x_t|Y_{0:t-1})}{p(y_t)} $$

In [24]:
def update(Y, t, log_p_predict, log_p_y, log_p_emission):
    """
    Args:
        Y (np.array): Observed sequence of words in array of shape [T].
        t (int): Current timestep.
        log_p_predict (np.array): `log p(x_t|y_{0:t-1})` array of shape [T+1,len(tag_vocab)].
        log_p_y (np.array): `log p(y_t)` array of shape [len(word_vocab)].
        log_p_emission (np.array): `log p(y_t|x_t)` array of shape [len(word_vocab),len(tag_vocab)].
    
    Returns: 
        np.array: `log p(x_t|y_{0:t})` for timestep t. Array of shape [len(tag_vocab)]
    """
    
    # Initialize an array to store the unnormalized log probabilities for x_t
    log_p_update = np.zeros(len(tag_vocab))
    
    # Calculate the unnormalized log probabilities for each x_t
    for state_t in range(len(tag_vocab)):
        # Accumulate log probabilities for the current state x_t
        log_p_update[state_t] = log_p_emission[Y[t], state_t] + log_p_predict[t, state_t] - log_p_y[Y[t]]

    print(log_p_update)
    # Return the unnormalized log probabilities
    return log_p_update

#### [2] (c) Smoothing: 
Please compute the smoothing step here. Note that you need to apply the log-sum-exp trick here and use numpy operations to efficiently compute the probabilities for all possible $x_t$ at the current timestep $t$. 

$$ p(x_t|Y) = p(x_t|Y_{0:t}) \sum_{x_{t+1} \in \mathcal{X}} p(x_{t+1}|x_t) \frac{p(x_{t+1}|Y)}{ p(x_{t+1}| Y_{0:t}) } $$

In [25]:
def smoothing(t, log_p_predict, log_p_update, log_p_marginal, log_p_transition): 
    """
    Args:
        t (int): Current timestep.
        log_p_predict (np.array): `log p(x_t|y_{0:t-1})` array of shape [T+1,len(tag_vocab)].
        log_p_update (np.array): `log p(x_t|y_{0:t})` array of shape [T+1,len(tag_vocab)].
        log_p_marginal (np.array): `log p(x_t|Y)` array of shape [T+1,len(tag_vocab)].
        log_p_transition (np.array): `log p(x_t|x_{t-1})` array of shape [len(tag_vocab),len(tag_vocab)].
    
    Returns: 
        np.array: `log p(x_t|Y)` for timestep t. Array of shape [len(tag_vocab)] 
    """

    # To obtain b
    ### For every possible x_t there is a unique b
    b = np.zeros(len(tag_vocab))

    for state_t in range(len(tag_vocab)):
        b[state_t] = np.finfo(float).min
        # Iterate over possible output state x_{t+1}
        for state_t_plus_1 in range(len(tag_vocab)):
            # get the maximum log-summand
            b[state_t] = np.maximum(b[state_t], log_p_transition[state_t, state_t_plus_1] + log_p_marginal[t, state_t_plus_1] - log_p_update[t, state_t_plus_1] )
    #print(b)

    # Use log-sum-exp trick to avoid numerical instability

    # Initialize log_p_predict with values equal to b
    log_p_smoothing = b

    # Now add the log-sums to every output (current state x_t)
    for state_t in range(len(tag_vocab)):
        # To calculate the log-sum, initialize the sum
        total_sum = 0
        
        # Iterate over possible future states x_{t+1} to get the sum
        for state_t_plus_1 in range(len(tag_vocab)):
            # Accumulate log probabilities for the current state x_t
            total_sum += np.exp(log_p_transition[state_t, state_t_plus_1] + log_p_marginal[t, state_t_plus_1] - log_p_update[t, state_t_plus_1] - b[state_t])
        
        # we need to add the log of the sum
        log_p_smoothing[state_t] += np.log(total_sum)

    #print(log_p_smoothing)
    
    return log_p_smoothing

#### Plugging it together
The functions above are applied in the following function that executes our algorithm to compute the marginals.
Please do not change anything in this function or the signature of the functions above. 
Take a look at their docstrings to understand what you need to compute.

In [26]:
def compute_marginals(Y_, log_p_transition, log_p_emission, log_p_y, log_p_x, tag_vocab):
    T = len(Y_)
    Y = np.zeros(T+1, dtype=int)
    Y[1:] = Y_ # since we are counting time from 1
    log_p_predict = np.zeros((T+1,len(tag_vocab)))
    log_p_update = np.zeros((T+1,len(tag_vocab)))
    log_p_update[0] = log_p_x  
    for t in range(1,T+1):
        log_p_predict[t] = predict(t, log_p_update, log_p_transition)
        log_p_update[t] = update(Y, t, log_p_predict, log_p_y, log_p_emission)
        
    log_p_marginal = np.zeros((T+1,len(tag_vocab)))
    for t in range(T-1,0,-1):
        log_p_marginal[t] = smoothing(t, log_p_predict, log_p_update, log_p_marginal, log_p_transition) 
    return log_p_marginal[1:]

## 3. Evaluate 
Now we can evaluate the algorithm we implemented on the test data.

Hint: you should get an accuracy > 90% if your implementation is correct.

In [27]:
def to_tokens(X, vocab):
    inv_map = {v: k for k, v in vocab.items()}
    return [inv_map[x] for x in X]

In [28]:
Y_test = np.array([word_vocab[w] for w,t in test_data])
X_test = np.array([tag_vocab[t] for w,t in test_data])
p_X_Y = compute_marginals(Y_test, log_p_transition, log_p_emission, log_p_y, log_p_x, tag_vocab)
X_pred = np.argmax(p_X_Y, axis=1)
acc = np.sum(X_pred == X_test) / X_pred.shape[0] * 100
print(to_tokens(X_test[:10], tag_vocab))
print(to_tokens(X_pred[:10], tag_vocab))
print(to_tokens(Y_test[:10], word_vocab))
print(f"Accuracy: {acc}%")

[  4.98112604 -22.62956724 -22.80309076 -22.70825152 -22.90591692
 -24.45655129 -23.7548944  -23.75066379 -23.57776839 -23.2771618
   1.2892171  -21.93267027]
[-21.6234275  -21.61030691 -21.78383043 -21.68899119 -21.88665659
 -23.43729096 -22.73563407 -22.73140346 -22.55850806 -22.25790147
   7.24474831 -20.91340994]
[-22.51452799 -22.50140739 -22.67493091 -22.58009167 -22.77775707
 -24.32839145 -23.62673456 -23.62250394 -23.44960855 -23.14900195
 -21.27737329   5.82651069]
[-23.09434648 -23.08122589 -23.2547494  -23.15991016   4.27344555
 -24.90820994 -24.20655305 -24.20232244 -24.02942704 -23.72882044
 -21.85719179 -22.38432892]
[-22.24704862 -22.23392803 -22.40745154 -22.3126123  -22.5102777
 -24.06091208   4.27176593 -23.35502458 -23.18212918 -22.88152258
 -21.00989393 -21.53703106]
[-22.57395141 -22.56083081 -22.73435433 -22.63951509 -22.83718049
 -24.38781487 -23.68615798 -23.68192736 -23.50903197 -23.20842537
 -21.33679671   5.76708727]
[-23.45978293 -23.44666234   3.99806573 -2